In [ ]:
import usb.core
import usb.util
import libusb
# Define the Vendor ID (VID) and Product ID (PID) of the Samsung mobile device

# Replace these values with the appropriate ones based on your device
VID = 0x04E8
PID = 0x6860

# Find the USB device based on the VID and PID
device = usb.core.find(idVendor=VID, idProduct=PID)

if device is None:
    print("Samsung mobile device not found.", device)
else:
    print("Samsung mobile device found.")


In [ ]:
device

In [ ]:
import usb.core
import usb.util

# USB device vendor and product ID
VENDOR_ID = 0x04E8
PRODUCT_ID = 0x6860
# USB endpoint for receiving data
ENDPOINT_IN = 0x86  # Change this to the correct endpoint address

# USB configuration and interface
CONFIGURATION = 1
INTERFACE = 0

# USB timeout (in milliseconds)
TIMEOUT_MS = 100000

# Find USB device
device = usb.core.find(idVendor=VENDOR_ID, idProduct=PRODUCT_ID)
if device is None:
    print("USB device not found.")
    exit()

# Set the active configuration
device.set_configuration(CONFIGURATION)

# Claim interface
usb.util.claim_interface(device, INTERFACE)

try:
    # Read data from USB endpoint
    print('uable to see')
    while True:
        try:
            print("No way to connect")
            data = device.read(ENDPOINT_IN, 64, TIMEOUT_MS)
            if data:
                print("After the data")
                print("Received message:", data)
        except usb.core.USBError as e:
            if e.errno == 110:  # Operation timed out
                continue
            else:
                print("USB read error:", e)
                break
finally:
    # Release the interface
    usb.util.release_interface(device,INTERFACE )


In [ ]:
import usb.core
import usb.util


# USB Vendor and Product IDs of the Android device
ANDROID_DEVICE_VENDOR_ID = 0x04E8
ANDROID_DEVICE_PRODUCT_ID = 0x6860

# USB endpoint address
ENDPOINT_ADDRESS = 0x86  # Endpoint address for data transfer (may vary based on your device)

# Find the Android device
def find_android_device():
    device = usb.core.find(idVendor=ANDROID_DEVICE_VENDOR_ID, idProduct=ANDROID_DEVICE_PRODUCT_ID)
    if device is None:
        raise ValueError("Android device not found")
    return device

# Perform handshake with the Android device
def perform_handshake():
    device = find_android_device()
    endpoint = device[0][(0, 0)][0]
    
    # Send connection request
    device.write(ENDPOINT_ADDRESS, b"CONNECT")
    
    # Wait for acknowledgment
    data = device.read(endpoint.bEndpointAddress, endpoint.wMaxPacketSize)
    if data and data.decode("utf-8") == "ACK":
        print("Connection established successfully")
    else:
        print("Failed to establish connection")

if __name__ == "__main__":
    perform_handshake()


In [ ]:
import usb.core

VID = 0x04E8
PID = 0x6860
# Find USB device
dev = usb.core.find(idVendor=0x04E8, idProduct=0x6860, TIMEOUT_MS)

if dev is None:
    raise ValueError('Device not found')

# Read data from USB device
try:
    while True:
        data = dev.read(0x86, 64)  # Endpoint address and packet size may vary
        print("Received from USB:", data)
except KeyboardInterrupt:
    pass


In [ ]:
import serial
import time

# Define the serial port name
serial_port = 'COM8'  # Replace 'X' with the actual port number
baud_rate = 9600

try:
    ser = serial.Serial(serial_port, baud_rate)
    print(f"Connected to {serial_port} at {baud_rate} baud.")
except serial.SerialException as e:
    print("Error opening serial port:", e)
    exit()

try:
    while True:
        try:
            command = ser.readline().decode().strip()
            print("Command received:", command)
            
            # Process the command and prepare a response
            if command == "HELLO":
                response = "Hello from Python!\n"
            elif command == "GOODBYE":
                response = "Goodbye from Python!\n"
            else:
                response = "Unknown command!\n"
            
            # Send the response back to the Android device
            ser.write(response.encode())
        except serial.SerialException as e:
            print("Error reading from serial port:", e)
            break
except KeyboardInterrupt:
    ser.close()
    print("Serial port closed.")

In [ ]:
import serial.tools.list_ports as ls;
print([p.device for p in ls.comports()])

In [ ]:
import socket
import threading

HOST = '0.0.0.0'  # Listen on all network interfaces
PORT = 12345  # Port to listen on

def handle_client(client_socket):
    while True:
        data = client_socket.recv(1024).decode('utf-8')
        if not data:
            break
        print("Received message:", data)

    client_socket.close()

def start_server():
    with socket.socket(socket.AF_INET, socket.SOCK_STREAM) as server_socket:
        server_socket.bind((HOST, PORT))
        server_socket.listen()

        print("Server started. Waiting for connection...")

        while True:
            client_socket, addr = server_socket.accept()
            print(f"Connected to {addr}")

            client_handler = threading.Thread(target=handle_client, args=(client_socket,))
            client_handler.start()

if __name__ == "__main__":
    start_server()


Server started. Waiting for connection...
Connected to ('172.20.10.5', 32773)


In [1]:
import socket
import logging
import sys

# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Server configuration
HOST = '0.0.0.0'  # Symbolic name, meaning all available interfaces
PORT = 12345  # Arbitrary non-privileged port
TIMEOUT = 100000  # Timeout for socket operations (60 seconds)

def main():
    try:
        # Create a socket object
        server_socket = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
       
        # Set socket timeout
        server_socket.settimeout(TIMEOUT)

        # Bind the socket to the host and port
        server_socket.bind((HOST, PORT))

        # Listen for incoming connections
        server_socket.listen(1)
        logger.info(f'Server is listening on {HOST}:{PORT}')

        # Accept incoming connection
        client_socket, client_address = server_socket.accept()
        logger.info(f'Connected to {client_address}')

        while True:
            # Receive data from the client
            data = client_socket.recv(1024)
            if not data:
                break
            logger.info(f'Received from client: {data.decode()}')

            # Echo back to the client
            client_socket.sendall(data)
            logger.info('Sent response to client')

        # Close the connection
        client_socket.close()
        server_socket.close()
    except socket.timeout:
        logger.error('Socket operation timed out')
    except Exception as e:
        logger.error(f'An error occurred: {e}')
        sys.exit(1)

if __name__ == "__main__":
    main()


2024-04-16 19:49:42,589 - INFO - Server is listening on 0.0.0.0:12345
2024-04-16 19:54:20,698 - INFO - Connected to ('172.20.10.3', 47944)


In [ ]:
import socket
import logging
import sys

# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Server configuration
HOST = '0.0.0.0'  # Server IP address to listen on all available network interfaces
PORT = 12345  # Server port

def main():
    try:
        # Create a socket object
        server_socket = socket.socket(socket.AF_INET, socket.SOCK_STREAM)

        # Bind the socket to the address and port
        server_socket.bind((HOST, PORT))

        # Start listening for incoming connections
        server_socket.listen()
        logger.info(f'Server listening on {HOST}:{PORT}')

        while True:
            # Accept a new connection
            client_socket, client_address = server_socket.accept()
            logger.info(f'Connection established from {client_address}')

            try:
                while True:
                    # Receive data from the client
                    data = client_socket.recv(1024)
                    if not data:
                        break
                    try:
                        # Attempt to decode the received data as UTF-8
                        decoded_data = data.decode('utf-8')
                        logger.info(f'Received from client {client_address}: {decoded_data}')
                    except UnicodeDecodeError as e:
                        # Try decoding with other encodings or ignore the problematic bytes
                        try:
                            decoded_data = data.decode('latin-1')  # Fallback to Latin-1 encoding
                            logger.warning(f'Error decoding data from client {client_address} with UTF-8. Using Latin-1 instead.')
                            logger.info(f'Received from client {client_address}: {decoded_data}')
                        except UnicodeDecodeError:
                            logger.error(f'Error decoding data from client {client_address}: {e}')
            except ConnectionResetError:
                logger.error(f'Connection with {client_address} was reset by the client.')
            finally:
                # Close the client socket
                client_socket.close()
                logger.info(f'Connection with {client_address} closed.')

    except Exception as e:
        logger.error(f'An error occurred: {e}')
        sys.exit(1)
    finally:
        # Close the server socket
        server_socket.close()

if __name__ == "__main__":
    main()


2024-04-17 21:51:40,357 - INFO - Server listening on 0.0.0.0:12345
2024-04-17 21:51:52,855 - INFO - Connection established from ('172.20.10.3', 48757)
2024-04-17 21:51:55,463 - INFO - Received from client ('172.20.10.3', 48757):                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

2024-04-17 21:51:55,560 - INFO - Received from client ('172.20.10.3', 48757):                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           

2024-04-17 21:51:55,624 - INFO - Received from client ('172.20.10.3', 48757):                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
2024-04-17 21:51:55,631 - INFO - Received from client ('172.20.10.3', 487

2024-04-17 21:51:55,714 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
          øÿêÿòÿäÿÖÿÓÿÌÿÚÿÝÿÚÿîÿñÿùÿ        üÿüÿùÿòÿùÿøÿõÿùÿ  üÿ               üÿøÿòÿîÿçÿêÿáÿêÿäÿáÿêÿäÿòÿêÿêÿ  õÿõÿøÿòÿòÿòÿçÿäÿÞÿÚÿÞÿÿçÿëÿäÿÝÿäÿÝÿîÿòÿøÿ õÿüÿùÿîÿòÿçÿçÿÞÿäÿÞÿ×ÿäÿÞÿäÿäÿõÿøÿñÿ      üÿ  üÿõÿõÿõÿñÿîÿîÿîÿäÿäÿëÿäÿáÿêÿäÿäÿäÿÞÿäÿäÿäÿêÿäÿçÿëÿëÿîÿêÿîÿîÿñÿêÿòÿøÿêÿüÿõÿîÿòÿêÿäÿäÿäÿÓÿçÿÓÿÚÿäÿÚÿîÿáÿçÿçÿçÿçÿîÿîÿîÿòÿîÿçÿçÿêÿÞÿäÿÞÿÞÿäÿîÿñÿüÿ  üÿ          õÿòÿêÿëÿòÿîÿòÿõÿòÿøÿøÿüÿ   	   
2024-04-17 21:51:55,744 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
      üÿ           - Received from client ('172.20.10.3', 48757): äÿÞÿäÿîÿçÿñÿùÿõÿòÿòÿêÿäÿäÿáÿäÿáÿçÿèÿÚÿêÿçÿáÿùÿùÿüÿ          üÿîÿêÿáÿÖÿÓÿÐÿÖÿÐÿçÿÞÿáÿòÿñÿ          üÿ  üÿ  øÿ      üÿùÿ  õÿøÿõÿòÿòÿçÿîÿçÿÖÿáÿÚÿÐÿÜÿÙÿàÿêÿîÿøÿ   	  %      
     õÿõÿüÿòÿøÿõÿùÿñÿîÿëÿîÿîÿîÿüÿøÿ  øÿ  øÿõÿ  õÿùÿõÿøÿîÿøÿøÿîÿîÿîÿòÿçÿîÿòÿçÿçÿî

2024-04-17 21:51:55,787 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:51:55,789 - INFO - Received from client ('172.20.10.3', 48757):   øÿ  ðÿìÿøÿðÿðÿèÿìÿäÿàÿìÿðÿðÿøÿüÿôÿðÿôÿäÿðÿðÿèÿøÿøÿüÿüÿ   üÿ    øÿ  ôÿìÿìÿÜÿðÿèÿøÿ             üÿôÿøÿðÿìÿðÿìÿìÿøÿôÿ       üÿþÿøÿðÿøÿøÿìÿøÿôÿôÿ            üÿèÿðÿäÿÜÿäÿèÿìÿ                                      üÿøÿ üÿ  üÿ ôÿôÿðÿèÿäÿÜÿÔÿØÿÍÿàÿðÿèÿ       üÿüÿøÿôÿèÿôÿÜÿØÿÜÿØÿÔÿàÿäÿäÿðÿìÿèÿäÿØÿÔÿØÿÂÿÊÿÍÿÂÿàÿÐÿäÿðÿôÿøÿøÿüÿøÿôÿðÿäÿàÿÊÿÑÿÊÿÍÿàÿèÿøÿüÿ üÿ    ìÿüÿäÿÜÿèÿÐÿØÿàÿðÿðÿüÿ        ðÿøÿäÿØÿèÿäÿèÿôÿ         ôÿüÿìÿäÿäÿàÿàÿàÿôÿðÿ   + + '  #      üÿ   #   
2024-04-17 21:51:55,816 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:51:55,818 - INFO - Received from client ('172.20.10.3', 48757):      ðÿìÿÜÿÈÿÜÿÌÿÔÿäÿìÿ             øÿøÿôÿøÿüÿðÿôÿôÿ üÿüÿ þÿüÿøÿèÿìÿÐ

...

2024-04-17 21:52:10,634 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:10,634 - INFO - Received from client ('172.20.10.3', 48757):   ïÿ  ïÿêÿôÿÛÿôÿÖÿÛÿÑÿ¸ÿÌÿ½ÿÌÿÌÿÇÿÖÿàÿàÿåÿïÿïÿïÿïÿàÿêÿàÿÛÿïÿïÿôÿúÿ    úÿ                         ïÿÖÿåÿÛÿåÿïÿïÿ   ïÿ   úÿ  ôÿ  ïÿ  úÿ úÿåÿïÿÛÿÛÿàÿÛÿåÿàÿàÿåÿåÿåÿÛÿÖÿÖÿÇÿÖÿÛÿÑÿÖÿÖÿÛÿàÿêÿêÿõÿúÿôÿ    ôÿïÿïÿïÿêÿåÿÛÿÑÿÖÿÑÿÇÿÖÿÛÿÛÿêÿïÿïÿïÿôÿïÿúÿ              ôÿàÿÛÿàÿÌÿÛÿÖÿÑÿàÿÖÿàÿïÿàÿïÿàÿêÿïÿàÿïÿêÿïÿïÿôÿêÿêÿåÿÛÿïÿåÿêÿÛÿåÿÖÿàÿàÿÖÿåÿÑÿÑÿÖÿÖÿåÿêÿêÿúÿúÿúÿ úÿ   úÿ úÿôÿ  úÿ    ïÿôÿôÿêÿêÿêÿêÿïÿêÿêÿúÿôÿêÿúÿ  åÿ           ôÿôÿàÿàÿÖÿàÿÛÿåÿïÿ úÿ                    ôÿ                    úÿ    êÿ  êÿïÿôÿôÿ  ôÿúÿúÿúÿôÿ  êÿåÿêÿÛÿÛÿàÿÛÿÑÿêÿÖÿÛÿåÿÛÿåÿÛÿåÿåÿàÿÛÿÛÿÖÿÖÿÑÿÖÿàÿÑÿÛÿÑÿÛÿêÿÖÿåÿêÿÛÿÖÿÑÿàÿÖÿåÿåÿôÿúÿôÿúÿôÿåÿåÿêÿåÿåÿÛÿÇÿÇÿÇÿ½ÿÂÿÌÿ¸ÿ¸ÿ¤ÿÿ©ÿÿ¸ÿ¸ÿ
2024-04-17 21:52:10,662 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-

2024-04-17 21:52:10,725 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:10,725 - INFO - Received from client ('172.20.10.3', 48757): ÌÿåÿêÿÛÿÖÿÌÿÂÿÂÿ¸ÿ½ÿ½ÿ¸ÿÖÿÑÿàÿôÿåÿåÿÛÿåÿåÿÛÿïÿôÿïÿôÿ      úÿúÿôÿïÿôÿïÿ       úÿ  õÿêÿåÿôÿêÿïÿàÿÛÿàÿÇÿÖÿÛÿÛÿÇÿàÿÛÿÑÿêÿïÿåÿïÿïÿåÿêÿôÿåÿ  úÿôÿúÿ    êÿõÿêÿôÿïÿàÿúÿ  úÿ        ïÿ  úÿ             úÿ               ïÿåÿåÿàÿÑÿÌÿÑÿÛÿÇÿÛÿàÿàÿêÿêÿúÿàÿêÿÖÿÑÿÛÿÇÿÖÿÛÿÑÿÖÿêÿàÿÖÿåÿïÿÛÿêÿôÿïÿúÿúÿúÿúÿðÿúÿïÿõÿúÿúÿ                 úÿêÿÛÿÛÿÌÿÂÿàÿÌÿÛÿåÿÖÿåÿêÿåÿêÿúÿåÿåÿôÿúÿêÿ  õÿÖÿàÿÛÿÛÿàÿúÿ  úÿ           / 4 4 9 * %      %                           úÿúÿ  ôÿôÿêÿúÿ  êÿ                                    ôÿ             / % % %    úÿúÿïÿõÿêÿúÿ  êÿúÿêÿåÿàÿåÿàÿÛÿúÿàÿïÿïÿåÿÛÿàÿàÿÇÿàÿÛÿõÿïÿôÿ õÿõÿïÿôÿåÿêÿêÿÛÿåÿÑÿÛÿêÿàÿôÿôÿåÿ
2024-04-17 21:52:10,742 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 in

2024-04-17 21:52:10,820 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:10,820 - INFO - Received from client ('172.20.10.3', 48757): Çÿ½ÿÌÿÑÿàÿêÿåÿêÿúÿïÿúÿõÿåÿïÿàÿåÿÖÿÖÿåÿ        % / *            ïÿ   ú    úÿúÿêÿôÿ  ôÿïÿïÿôÿ  úÿúÿúÿ          ôÿúÿôÿïÿïÿïÿêÿêÿúÿ  õÿïÿåÿàÿÛÿÖÿàÿåÿåÿåÿôÿúÿêÿïÿ  êÿ  êÿêÿåÿÛÿêÿàÿïÿåÿåÿåÿïÿúÿúÿïÿêÿïÿÌÿÖÿêÿÌÿÖÿÛÿÑÿÑÿÑÿÇÿÛÿÌÿÛÿåÿÛÿÖÿÑÿÂÿ¸ÿ¸ÿ©ÿ¸ÿÂÿ½ÿÖÿÛÿúÿôÿ úÿôÿúÿêÿúÿïÿïÿåÿïÿïÿåÿïÿåÿïÿïÿúÿúÿúÿïÿúÿúÿþÿ     úÿ           * * /                êÿõÿúÿàÿõÿ  úÿ                 úÿ     úÿ   úÿúÿ
2024-04-17 21:52:10,820 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:10,835 - INFO - Received from client ('172.20.10.3', 48757): ôÿêÿàÿåÿÖÿêÿôÿåÿúÿúÿõÿúÿ      ôÿ  õÿàÿêÿåÿðÿêÿïÿðÿïÿïÿêÿêÿàÿåÿåÿ     ïÿúÿêÿêÿÖÿàÿÖÿÇÿÑÿàÿïÿåÿ  úÿåÿôÿÑÿÖÿÂÿ¸ÿÇÿ½ÿÑÿÇÿÖÿÂÿÇÿÌÿÂÿÖÿåÿêÿïÿ          ôÿ  ôÿúÿ  úÿ  úÿ    úÿõÿúÿú

2024-04-17 21:52:10,899 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:10,899 - INFO - Received from client ('172.20.10.3', 48757): ¤ÿÿÿYÿ_ÿTÿDÿOÿ4ÿDÿ4ÿÿ$ÿJÿÿ¯ÿïÿ  , = = 1  úÿÚÿäÿ  ' "  éÿúÿ      Ôÿ´ÿÿjÿYÿ^ÿ^ÿdÿtÿÿÿ´ÿÔÿäÿïÿ  " 7    úÿôÿúÿ ,     ïÿêÿÉÿÞÿÏÿÊÿúÿ, g  ± · ¼ ­  g W L ]   § w g L       Éÿ¤ÿNÿ.ÿ#ÿ.ÿ^ÿÿ¯ÿÄÿÊÿÄÿúÿúÿ  " L , L , úÿäÿªÿÿ^ÿCÿÿóþãþÿNÿyÿ¹ÿÄÿÉÿ¾ÿ´ÿÊÿßÿßÿïÿúÿ 7 7 7   ÄÿÿTÿ(ÿÿÿÿ#ÿ9ÿCÿ^ÿ^ÿÿÿÿÿ¯ÿ¹ÿïÿ   ïÿÏÿ¾ÿÙÿ   " "       êÿÔÿÙÿÄÿÔÿÄÿ©ÿÿYÿ#ÿ(ÿ>ÿ>ÿcÿ©ÿßÿ  1 Q g W s r W W B 2      "    7 ' '   Ùÿ¹ÿ~ÿyÿÿ¯ÿÊÿôÿêÿäÿÏÿªÿÿNÿ4ÿ)ÿ4ÿiÿ´ÿúÿ" = B   " G ¢ Ó Ý ø È ­ 
2024-04-17 21:52:10,930 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:10,930 - INFO - Received from client ('172.20.10.3', 48757):  } Q  úÿÔÿÔÿÔÿ ' ,    Ôÿ¤ÿÄÿßÿ ] m } r h R 7         ' , 2 7 1 G < 2 <   ï

2024-04-17 21:52:11,014 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:11,016 - INFO - Received from client ('172.20.10.3', 48757): îÿãÿØÿèÿÞÿØÿéÿØÿôÿ
 # `  É Ï õ å ß Ù ³  Z  îÿÒÿÈÿÍÿôÿ . U O O e 3 D 3  
 èÿ¼ÿÇÿãÿ  4 I _ I  Øÿÿ=ÿÿöþêþêþÿÿ8ÿ_ÿzÿ²ÿÂÿÞÿ    
        úÿúÿéÿîÿÝÿÒÿÇÿ²ÿÿÿzÿzÿuÿpÿÿÿ¼ÿÒÿîÿ   èÿîÿèÿ    #     ) 3 T    p J 4 . # ? D > . #  ôÿãÿÈÿ¦ÿ¬ÿ²ÿÈÿÓÿéÿúÿïÿúÿèÿ    ôÿ  úÿ      èÿèÿÂÿ²ÿ¬ÿ¡ÿ¡ÿ¡ÿ¦ÿ¦ÿÈÿÈÿØÿ²ÿ¢ÿqÿUÿ`ÿ[ÿ|ÿ¨ÿ¾ÿÞÿêÿÙÿÙÿ²ÿ¾ÿÿÿÿÿÿÿ²ÿ½ÿÔÿÎÿïÿ    -    êÿÙÿÙÿÔÿêÿúÿêÿäÿÔÿ¸ÿ¾ÿÿÿÿvÿÿ¢ÿÙÿ I o j i C    " 8 d t z o o j d z j d H N S 3 _ j i z i S "   úÿÙÿ¸ÿ¨ÿÿ­ÿÈÿÞÿïÿúÿôÿ
2024-04-17 21:52:11,018 - WARNING - Error decoding data from client ('172.20.10.3', 48757) with UTF-8. Using Latin-1 instead.
2024-04-17 21:52:11,018 - INFO - Received from client ('172.20.10.3', 48757): Þÿäÿêÿ     "     úÿïÿäÿêÿäÿäÿïÿÎÿÞÿäÿÞÿ   8 N d u z z Y 8 äÿ­ÿ¢ÿÿÿ³ÿ¸ÿÎÿ¾ÿÈÿÈÿÉÿÙÿÞÿäÿÙ

In [1]:
import socket
import logging
import sys
import pyaudio
import wave

# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Server configuration
HOST = '0.0.0.0'  # Server IP address to listen on all available network interfaces
PORT = 12345  # Server port

# PyAudio configuration
FORMAT = pyaudio.paInt16  # Audio format
CHANNELS = 1  # Number of audio channels (1 for mono, 2 for stereo)
RATE = 44100  # Sample rate (samples per second)
CHUNK_SIZE = 1024  # Number of frames per buffer

def record_audio(stream, filename):
    logger.info("Recording started...")
    frames = []
    for _ in range(0, int(RATE / CHUNK_SIZE * RECORD_SECONDS)):
        data = stream.read(CHUNK_SIZE)
        frames.append(data)
    logger.info("Recording stopped.")

    # Save the recorded audio to a WAV file
    wf = wave.open(filename, 'wb')
    wf.setnchannels(CHANNELS)
    wf.setsampwidth(stream.get_sample_size(FORMAT))
    wf.setframerate(RATE)
    wf.writeframes(b''.join(frames))
    wf.close()
    logger.info(f"Audio saved to {filename}")

def main():
    try:
        # Create a socket object
        server_socket = socket.socket(socket.AF_INET, socket.SOCK_STREAM)

        # Bind the socket to the address and port
        server_socket.bind((HOST, PORT))

        # Start listening for incoming connections
        server_socket.listen()
        logger.info(f'Server listening on {HOST}:{PORT}')

        # Initialize PyAudio
        audio = pyaudio.PyAudio()

        while True:
            # Accept a new connection
            client_socket, client_address = server_socket.accept()
            logger.info(f'Connection established from {client_address}')

            try:
                # Open a stream for audio capture
                stream = audio.open(format=FORMAT,
                                    channels=CHANNELS,
                                    rate=RATE,
                                    input=True,
                                    frames_per_buffer=CHUNK_SIZE)

                # Record audio from the stream
                record_audio(stream, f"audio_{client_address}.wav")
                
                # Close the stream
                stream.stop_stream()
                stream.close()

            except ConnectionResetError:
                logger.error(f'Connection with {client_address} was reset by the client.')
            finally:
                # Close the client socket
                client_socket.close()
                logger.info(f'Connection with {client_address} closed.')

    except Exception as e:
        logger.error(f'An error occurred: {e}')
        sys.exit(1)
    finally:
        # Close the server socket
        server_socket.close()
        # Terminate PyAudio
        audio.terminate()

if __name__ == "__main__":
    main()


2024-04-18 02:12:31,764 - INFO - Server listening on 0.0.0.0:12345
2024-04-18 02:12:34,352 - INFO - Connection established from ('172.20.10.3', 48789)
2024-04-18 02:12:34,523 - INFO - Recording started...
2024-04-18 02:12:34,523 - INFO - Connection with ('172.20.10.3', 48789) closed.
2024-04-18 02:12:34,523 - ERROR - An error occurred: name 'RECORD_SECONDS' is not defined
2024-04-18 02:12:34,614 - ERROR - Internal Python error in the inspect module.
Below is the traceback from this internal error.

2024-04-18 02:12:34,789 - INFO - 
Unfortunately, your original traceback can not be constructed.



Traceback (most recent call last):
  File "C:\Users\birha\AppData\Local\Temp\ipykernel_7008\3206977153.py", line 67, in main
    record_audio(stream, f"audio_{client_address}.wav")
  File "C:\Users\birha\AppData\Local\Temp\ipykernel_7008\3206977153.py", line 24, in record_audio
    for _ in range(0, int(RATE / CHUNK_SIZE * RECORD_SECONDS)):
NameError: name 'RECORD_SECONDS' is not defined

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py", line 3457, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "C:\Users\birha\AppData\Local\Temp\ipykernel_7008\3206977153.py", line 90, in <module>
    main()
  File "C:\Users\birha\AppData\Local\Temp\ipykernel_7008\3206977153.py", line 82, in main
    sys.exit(1)
SystemExit: 1

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "C:\

TypeError: object of type 'NoneType' has no len()